## **NEXT WORD PREDICTOR USING LSTM**

### **Importing the dependecies**

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow import keras
from keras.utils import pad_sequences, to_categorical
from tensorflow.keras.preprocessing.text import Tokenizer
from keras.layers import Dense, Input, Dropout, LSTM, Embedding
from keras import Sequential

2026-01-15 18:44:18.913931: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [2]:
gpus = tf.config.experimental.list_physical_devices("GPU")
if gpus:
    for gpu in gpus:
        tf.config.experimental.set_memory_growth(gpu, True)

### **Reading and preprocessign of data**

In [3]:
with open("/mnt/c/Users/Subham Pathak/Desktop/AI/DEEP_LEARNING/notebooks/RNN/datasets/1661-0.txt", 'r') as file:
    docs = file.read()
    file.close()
    
    print(docs)


Project Gutenberg's The Adventures of Sherlock Holmes, by Arthur Conan Doyle

This eBook is for the use of anyone anywhere at no cost and with
almost no restrictions whatsoever.  You may copy it, give it away or
re-use it under the terms of the Project Gutenberg License included
with this eBook or online at www.gutenberg.net


Title: The Adventures of Sherlock Holmes

Author: Arthur Conan Doyle

Release Date: November 29, 2002 [EBook #1661]
Last Updated: May 20, 2019

Language: English

Character set encoding: UTF-8

*** START OF THIS PROJECT GUTENBERG EBOOK THE ADVENTURES OF SHERLOCK HOLMES ***



Produced by an anonymous Project Gutenberg volunteer and Jose Menendez



cover



The Adventures of Sherlock Holmes



by Arthur Conan Doyle



Contents


   I.     A Scandal in Bohemia
   II.    The Red-Headed League
   III.   A Case of Identity
   IV.    The Boscombe Valley Mystery
   V.     The Five Orange Pips
   VI.    The Man with the Twisted Lip
   VII.   The Adventure of the Blue C

In [4]:
docs_splited = docs.split("\n")

sentence = [s.strip() for s in docs_splited if s.strip()]
print(sentence)

['\ufeff', "Project Gutenberg's The Adventures of Sherlock Holmes, by Arthur Conan Doyle", 'This eBook is for the use of anyone anywhere at no cost and with', 'almost no restrictions whatsoever.  You may copy it, give it away or', 're-use it under the terms of the Project Gutenberg License included', 'with this eBook or online at www.gutenberg.net', 'Title: The Adventures of Sherlock Holmes', 'Author: Arthur Conan Doyle', 'Release Date: November 29, 2002 [EBook #1661]', 'Last Updated: May 20, 2019', 'Language: English', 'Character set encoding: UTF-8', '*** START OF THIS PROJECT GUTENBERG EBOOK THE ADVENTURES OF SHERLOCK HOLMES ***', 'Produced by an anonymous Project Gutenberg volunteer and Jose Menendez', 'cover', 'The Adventures of Sherlock Holmes', 'by Arthur Conan Doyle', 'Contents', 'I.     A Scandal in Bohemia', 'II.    The Red-Headed League', 'III.   A Case of Identity', 'IV.    The Boscombe Valley Mystery', 'V.     The Five Orange Pips', 'VI.    The Man with the Twisted Lip', '

In [5]:
# calling the tokenizer class
token = Tokenizer(oov_token='hihihihihi')


In [6]:
token.fit_on_texts(sentence)
token.word_index

{'hihihihihi': 1,
 'the': 2,
 'and': 3,
 'to': 4,
 'of': 5,
 'a': 6,
 'i': 7,
 '”': 8,
 'in': 9,
 'that': 10,
 'it': 11,
 'he': 12,
 'was': 13,
 'you': 14,
 'his': 15,
 'is': 16,
 'my': 17,
 'have': 18,
 'with': 19,
 'as': 20,
 'had': 21,
 'at': 22,
 'which': 23,
 'for': 24,
 'be': 25,
 'not': 26,
 'me': 27,
 'but': 28,
 'from': 29,
 'we': 30,
 'this': 31,
 'said': 32,
 'upon': 33,
 'there': 34,
 'holmes': 35,
 'him': 36,
 'so': 37,
 'her': 38,
 'she': 39,
 'all': 40,
 '’': 41,
 'been': 42,
 'your': 43,
 'on': 44,
 'very': 45,
 'by': 46,
 'one': 47,
 'are': 48,
 '“i': 49,
 'were': 50,
 'an': 51,
 'no': 52,
 'would': 53,
 'out': 54,
 'what': 55,
 'then': 56,
 'up': 57,
 'when': 58,
 'man': 59,
 'could': 60,
 'has': 61,
 'do': 62,
 'into': 63,
 'or': 64,
 'little': 65,
 'will': 66,
 'who': 67,
 'mr': 68,
 'if': 69,
 'some': 70,
 'down': 71,
 'see': 72,
 'now': 73,
 'our': 74,
 'should': 75,
 'may': 76,
 'am': 77,
 'us': 78,
 'over': 79,
 'they': 80,
 'can': 81,
 'more': 82,
 'think': 83,

In [7]:
(len(token.word_index))

8932

In [8]:
tokenize_sentence = token.texts_to_sequences(sentence)
print(tokenize_sentence)

[[4790], [146, 4791, 2, 1021, 5, 129, 35, 46, 612, 2236, 2237], [31, 1022, 16, 24, 2, 276, 5, 395, 2238, 22, 52, 1677, 3, 19], [573, 52, 3399, 3400, 14, 76, 818, 11, 214, 11, 125, 64], [2239, 276, 11, 263, 2, 481, 5, 2, 146, 131, 656, 2240], [19, 31, 1022, 64, 2241, 22, 1094, 131, 3401], [2667, 2, 1021, 5, 129, 35], [4792, 612, 2236, 2237], [4793, 1023, 4794, 4795, 4796, 1022, 2242], [140, 3402, 76, 3403, 4797], [3404, 1095], [574, 244, 4798, 4799, 1470], [723, 5, 31, 146, 131, 1022, 2, 1021, 5, 129, 35], [1929, 46, 51, 3405, 146, 131, 2668, 3, 3406, 3407], [1678], [2, 1021, 5, 129, 35], [46, 612, 2236, 2237], [1930], [7, 6, 886, 9, 941], [2669, 2, 249, 482, 692], [2670, 6, 114, 5, 2243], [3408, 2, 775, 1471, 523], [3409, 2, 313, 1024, 942], [3410, 2, 59, 19, 2, 1096, 943], [3411, 2, 613, 5, 2, 449, 1472], [3412, 2, 613, 5, 2, 1931, 887], [3413, 2, 613, 5, 2, 3414, 693], [3415, 2, 613, 5, 2, 819, 1341], [3416, 2, 613, 5, 2, 2244, 407], [3417, 2, 613, 5, 2, 888, 944], [7, 6, 886, 9, 941

In [9]:
len(tokenize_sentence)

9634

In [10]:
input_sentence = []
for sent in tokenize_sentence:
    for i in range(1, len(sent)):
        input_sentence.append(sent[ : i+1])

In [11]:
print(input_sentence)

[[146, 4791], [146, 4791, 2], [146, 4791, 2, 1021], [146, 4791, 2, 1021, 5], [146, 4791, 2, 1021, 5, 129], [146, 4791, 2, 1021, 5, 129, 35], [146, 4791, 2, 1021, 5, 129, 35, 46], [146, 4791, 2, 1021, 5, 129, 35, 46, 612], [146, 4791, 2, 1021, 5, 129, 35, 46, 612, 2236], [146, 4791, 2, 1021, 5, 129, 35, 46, 612, 2236, 2237], [31, 1022], [31, 1022, 16], [31, 1022, 16, 24], [31, 1022, 16, 24, 2], [31, 1022, 16, 24, 2, 276], [31, 1022, 16, 24, 2, 276, 5], [31, 1022, 16, 24, 2, 276, 5, 395], [31, 1022, 16, 24, 2, 276, 5, 395, 2238], [31, 1022, 16, 24, 2, 276, 5, 395, 2238, 22], [31, 1022, 16, 24, 2, 276, 5, 395, 2238, 22, 52], [31, 1022, 16, 24, 2, 276, 5, 395, 2238, 22, 52, 1677], [31, 1022, 16, 24, 2, 276, 5, 395, 2238, 22, 52, 1677, 3], [31, 1022, 16, 24, 2, 276, 5, 395, 2238, 22, 52, 1677, 3, 19], [573, 52], [573, 52, 3399], [573, 52, 3399, 3400], [573, 52, 3399, 3400, 14], [573, 52, 3399, 3400, 14, 76], [573, 52, 3399, 3400, 14, 76, 818], [573, 52, 3399, 3400, 14, 76, 818, 11], [573, 5

In [12]:
max_len = max([len(x) for x in input_sentence])
print(max_len)

20


In [13]:
padded_seq = pad_sequences(input_sentence, padding='pre', maxlen=max_len)

In [14]:
padded_seq.shape

(101619, 20)

In [15]:
x = padded_seq[:, :-1]
y = padded_seq[:,-1]
x.shape

(101619, 19)

In [16]:
len(token.word_index)

8932

In [17]:
y = to_categorical(y, num_classes=8933)

In [18]:
x

array([[   0,    0,    0, ...,    0,    0,  146],
       [   0,    0,    0, ...,    0,  146, 4791],
       [   0,    0,    0, ...,  146, 4791,    2],
       ...,
       [   0,    0,    0, ..., 8932,    4,  361],
       [   0,    0,    0, ...,    4,  361,   84],
       [   0,    0,    0, ...,  361,   84,  359]],
      shape=(101619, 19), dtype=int32)

In [19]:
y.shape

(101619, 8933)

In [20]:
vocab_size = len(token.word_index)+1
vocab_size

8933

### **Building the LSTM model**

In [21]:
model = Sequential()
model.add(Input(shape=(max_len, )))

model.add(Embedding(vocab_size, 50))
model.add(LSTM(100))

model.add(Dense(vocab_size, activation='softmax'))

I0000 00:00:1768502670.591919     847 gpu_device.cc:2020] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 1766 MB memory:  -> device: 0, name: NVIDIA GeForce RTX 2050, pci bus id: 0000:01:00.0, compute capability: 8.6


In [22]:
model.compile(loss='sparse_categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

In [23]:
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ embedding (Embedding)           │ (None, 20, 50)         │       446,650 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm (LSTM)                     │ (None, 100)            │        60,400 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 8933)           │       902,233 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 1,409,283 (5.38 MB)

 Trainable params: 1,409,283 (5.38 MB)

 Non-trainable params: 0 (0.00 B)

In [ ]:
history = model.fit(x, y, epochs=10)